In [2]:
#Input_info
"""
Created on Wed Oct  5 13:51:55 2022

@author: askung
"""

from Bio.Seq import Seq
import pandas as pd
import numpy as np
import seaborn as sns
import matplotlib.pyplot as plt 
import matplotlib.colors
import math
import glob
import os
import re
import importlib.util


####General data####
#Import primers (For barcode positions)
Fw_Primers = pd.read_excel ('C:/Users/askung/OneDrive - Danmarks Tekniske Universitet/WP1/NGS/Barcode_Analysis/Fw_Primers.xlsx')
Rev_Primers = pd.read_excel ('C:/Users/askung/OneDrive - Danmarks Tekniske Universitet/WP1/NGS/Barcode_Analysis/Rev_Primers.xlsx')


#Which was the first primer for NGS?
First_primer_used = 1 #(For NGS data)
#How long was the sequence?
ORF_Length = 2169

#################
######Paths######
#NGS_data general path
NGS_path = "C:/Users/askung/OneDrive - Danmarks Tekniske Universitet/WP1/NGS/"

#Path to find merger data (specific to the GG768 run)
Alignment_Data=f'{NGS_path}/GG_768_P85a/Alignment'
Path_With_CSVname=f'{NGS_path}GG_768_P85a/Alignment/Merged_Nanopore.csv'


#Path to find luminescence data from Hamilton (Different path than the rest)
luminescence_path = "C:/Users/askung/OneDrive - Danmarks Tekniske Universitet/WP1/Automation_Work/2022_10_13_GGlib_Third"

#Data after the demultiplex (Keep after_demultiplex but change the "GG768"-part)
Seq_Data = pd.read_csv(f'{NGS_path}GG_768_P85a/Output/pass/after_demultiplex.csv',sep=",")

#FastQ files (For merger)
FastQ_path = f'{NGS_path}GG_768_P85a/Output/pass'
#Alignment_merged (for Demultiplex)
Sequence_samples = pd.read_csv(f'{NGS_path}GG_768_P85a/Alignment/Merged_Nanopore.csv',sep=",")


#########Script-paths below, not needed to fill########
#Path for running "Nanopore_Merger_script"
Merger_path = f'{NGS_path}NGS_Hamilton_Script_package/Nanopore_Merger.py'
#Path for running "Demultiplex_script"
Demultiplex_Path = f'{NGS_path}NGS_Hamilton_Script_package/Double_barcode_Demultiplexer.py'
#Path for running "After_Demultiplex_script"
AfterDemultiplex_Path = f'{NGS_path}NGS_Hamilton_Script_package/Demultiplexed_To_Stuctured_With_Lum_data.py'
#Outputs for data analysis
Output_Path = f'{NGS_path}GG_768_P85a/Output/pass'

print("Input_Run done")

#Optimizations: 
    #Test the second-best option as well as the best (Seems they don´t always fit)
    #Combine Fw/reverse to make them fit together (Fixed I think )
        #Alternatively switch End/start to see results
    #Extra QC: Check if Fw/rev shows the same

Input_Run done


In [ ]:
#Merger_data


####Import packages####
from Bio import pairwise2
from Bio.Seq import Seq
import pandas as pd
import numpy as np
import os
from Bio import SeqIO
import csv
import glob

####Directory set####


os.chdir(Alignment_Data)
Summary = pd.read_csv('alignment_summary.txt',sep="\t")

os.chdir(FastQ_path)
Filelist =(glob.glob("*.fastq"))

SeqData = []
for i in Filelist:
    for record in SeqIO.parse(i, "fastq"):
        SeqData.append([record.id,record.seq])

SeqData = pd.DataFrame(data=SeqData)

SeqData.columns=["read_id","Sequence"]

Merged_Data= pd.merge(SeqData,Summary,on=["read_id"])

Merged_Data.to_csv(Path_With_CSVname, index = False)

In [ ]:
# Demultiplexer
def NGS_Demultiplexer(Fw,Rev,Sequences): 
    #Put in plate and position number 
    Sequence_samples["PlateNo"]=0
    Sequence_samples["PosNo"]=0
    
    
    
    Sequence_samplesMinus = Sequence_samples[Sequence_samples["alignment_direction"].str.contains("-")].reset_index()
    Sequence_samplesPlus = Sequence_samples[-(Sequence_samples["alignment_direction"].str.contains("-"))].reset_index()
    ##################################ADD ABOVE TO BELOW AND COMBINE!!#################
    #Find barcode possibilities:
    Fw_Barcodes = Fw_Primers.iloc[:,2]
    Rev_Barcodes = Rev_Primers.iloc[:,2]
    
    
    BC_Runs1 =0
    BC_Runs2 =0
    BC_Runs3 =0
    BC_Runs4 =0
    

    #For all of the Fw barcodes--> Find the ones that contains the barcodes
    for i in range(Fw_Barcodes.shape[0]):
        #Defines the 16 base barcode
        Barcode = Seq(Fw_Barcodes[i][0:9])
    
        Barcode = str(Barcode)
        #test.append(["This is",i])
        #Positions samples based on tags:
        for j in range(len(Sequence_samplesPlus["Sequence"])):
            First_Barcode = str(Sequence_samplesPlus["Sequence"][j]).find(Barcode)
            if First_Barcode>=0:
                Second_Barcode = (str(Sequence_samplesPlus["Sequence"][j][First_Barcode+1:First_Barcode+16]).find(Barcode))
                if Second_Barcode>=0:
                    Sequence_samplesPlus["PosNo"][j]= i+1
                    BC_Runs1 +=1
                    
    
    for i in range(Fw_Barcodes.shape[0]):
        #Defines the 16 base barcode
        Barcode = Seq(Fw_Barcodes[i][0:9]).reverse_complement()
        Barcode = str(Barcode)
        #Positions samples based on tags:
        #Sequence_samplesMinus["PosNo"][Sequence_samplesMinus["Sequence"].str.contains(Barcode)]=i+1 #Starts at 0
        for j in range(len(Sequence_samplesMinus["Sequence"])):
            First_Barcode = str(Sequence_samplesMinus["Sequence"][j]).find(Barcode)
    
            if First_Barcode>=0:
                Second_Barcode = (str(Sequence_samplesMinus["Sequence"][j][First_Barcode+1:First_Barcode+16]).find(Barcode))
                if Second_Barcode>=0:
                    Sequence_samplesMinus["PosNo"][j]= i+1
                    BC_Runs2 +=1
    
                    
    for i in range(Rev_Barcodes.shape[0]):
        #Defines the 16 base barcode
        Barcode = Seq(Rev_Barcodes[i][0:9]).reverse_complement()
        Barcode = str(Barcode)
        #Positions samples based on tags:
        for j in range(len(Sequence_samplesPlus["Sequence"])):
            First_Barcode = str(Sequence_samplesPlus["Sequence"][j]).find(Barcode)
            if First_Barcode>=0:
                Second_Barcode = (str(Sequence_samplesPlus["Sequence"][j][First_Barcode+1:First_Barcode+16]).find(Barcode))
                if Second_Barcode>=0:
                    Sequence_samplesPlus["PlateNo"][j]= i+1
                    BC_Runs3 +=1
    
    for i in range(Rev_Barcodes.shape[0]):
        #Defines the 16 base barcode
        Barcode = Seq(Rev_Barcodes[i][0:9])
        Barcode = str(Barcode)
        #Positions samples based on tags:
        for j in range(len(Sequence_samplesMinus["Sequence"])):
            First_Barcode = str(Sequence_samplesMinus["Sequence"][j]).find(Barcode)
    
            if First_Barcode>=0:
                Second_Barcode = (str(Sequence_samplesMinus["Sequence"][j][First_Barcode+1:First_Barcode+16]).find(Barcode))
                if Second_Barcode>=0:
                    Sequence_samplesMinus["PlateNo"][j]= i+1
                    BC_Runs4 +=1
                    
                    
    Sequence_samples_Demultiplexed=Sequence_samplesMinus.append(Sequence_samplesPlus)
    
    #Remove anything without hits related to specific positions and plates
    Test_Info= Sequence_samples_Demultiplexed[Sequence_samples_Demultiplexed["PosNo"]>0]
    Test_Info2=Test_Info[Test_Info["PlateNo"]>0].reset_index()
    
    Test_Info2[Test_Info2["alignment_genome"]!="*"] #Remove non-aligned pieces
    
    Test_Info2["Positions"] = Test_Info2["PlateNo"].astype(str)+","+Test_Info2["PosNo"].astype(str)
    Test_Info2["Duplicates"]=0
    
    for i in range(len(Test_Info2["Duplicates"])):
        Test_Info2["Duplicates"][Test_Info2["Positions"]==Test_Info2["Positions"][i]] +=1
    
    
    
    #Change Test_Info2_Properties:
    Test_Info2=Test_Info2[Test_Info2["Duplicates"]>3]
    #Plot: See data from above
    
    colors=np.array(Test_Info2["Duplicates"])
    colors=(colors/np.max(colors)) 
    
    plt.scatter(Test_Info2["PosNo"],Test_Info2["PlateNo"],c=colors)
    plt.xlabel("Fw_Primer")
    plt.ylabel("Rev_Primer")
    
    norm = matplotlib.colors.Normalize(vmin=1, vmax=1000)
    cmap = plt.cm.rainbow
    sm = plt.cm.ScalarMappable(cmap=cmap, norm=norm)
    sm.set_array([])  # only needed for matplotlib < 3.1
    plt.colorbar(sm)
    
    """
    Below is some tests for GST+TrxA
    #Test_InfoGST = Test_Info2[Test_Info2["alignment_genome"]=="GST_only"]
    #plt.scatter(Test_InfoGST["PosNo"],Test_InfoGST["PlateNo"],c="Red")
    #Test_InfoTrxA= Test_Info2[Test_Info2["alignment_genome"]=="TrxA_Only"]
    #plt.scatter(Test_InfoTrxA["PosNo"],Test_InfoTrxA["PlateNo"],c="Green")
    """
    
    #Explanation dataset
    A1_Full_Dataset=Sequence_samples
    A2_Fw_barcoded=Test_Info
    A3_Fw_Rev_Barcoded=Test_Info2
    A4_Rev_Barcoded=Sequence_samples_Demultiplexed[Sequence_samples_Demultiplexed["PlateNo"]>0]
    ###Current problem: Both tags are not very common at the same time
    
    Test_Info2.to_csv(f'{Output_Path}/after_demultiplex.csv', index = False)
    
    
NGS_Demultiplexer(Fw_Primers,Rev_Primers,Sequence_samples)

In [9]:
# Luminescence_Combiner

def NGS_Structure(After): 
    #Fix up data
    Seq_Data=After.sort_values("Positions")
    Seq_Data= Seq_Data[Seq_Data["alignment_genome"]!="*"]
    
    
    #Find all plate positions
    Positions = [Seq_Data.Positions.unique()]
    
    #Array to fill data about probable position into, added a 0-array to start
    Combined_NGS = np.array([0,0,0,0,0,0,0,0])
    
    #Two dataframes to fill temp-data into
    NGS_start = pd.DataFrame([[0,0,0,0]],columns=["PlatePos","Gene_Position","Percentage", "Amount"])
    NGS_end = pd.DataFrame([[0,0,0,0]],columns=["PlatePos","Gene_Position","Percentage", "Amount"])
    
    #Loop that goes through all the found plate-positions 
    for platepositions in range(len(Positions[0])):
        Start_Positions = []
        End_Positions = []
        
        Pos = Seq_Data[Seq_Data["Positions"]==Positions[0][platepositions]]
    
        Start_Pos = [Pos.alignment_genome_start.unique()]
        End_Pos = [Pos.alignment_genome_end.unique()]
        #Teststart gets fixed so it tests how many are at +- 5 bases on each side (Expecting minor errors)
        for copies in range(len(Start_Pos[0])):
            TestStart = Pos[Pos["alignment_genome_start"]>Start_Pos[0][copies]-5][Pos["alignment_genome_start"]<Start_Pos[0][copies]+5]
            Start_Pos_Predicter = (TestStart["alignment_genome_start"].value_counts())
            Len_Start = len(TestStart["alignment_genome_start"])
            Start_Positions.append([Positions[0][platepositions],Start_Pos_Predicter.index[0],Len_Start/Pos["Duplicates"].iloc[0],Pos["Duplicates"].iloc[0]])
        
        
        Start_Positions = np.array([Start_Positions])
        Start_Positions = pd.DataFrame(Start_Positions[0],columns=["PlatePos","Gene_Position","Percentage", "Amount"])
        
        Start_Positions["Percentage"] = pd.to_numeric(Start_Positions["Percentage"])
        Start_Positions = Start_Positions.sort_values("Percentage")
        
        Start_Pos_Best = np.array(Start_Positions.iloc[-1,:])
        
       
        for copies in range(len(End_Pos[0])):
            TestEnd = Pos[Pos["alignment_genome_end"]>End_Pos[0][copies]-5][Pos["alignment_genome_end"]<End_Pos[0][copies]+5]
            ###A test to remove the ones that don´t fit with the Fw. primer
            TestEnd = TestEnd[TestEnd["alignment_genome_start"]>int(Start_Pos_Best[1])-5][TestEnd["alignment_genome_start"]<int(Start_Pos_Best[1])+5]
            End_Pos_Predicter = (TestEnd["alignment_genome_end"].value_counts())
            Len_end = len(TestEnd["alignment_genome_end"])
    
            if Len_end>0:
                End_Positions.append([Positions[0][platepositions],End_Pos_Predicter.index[0],Len_end/Pos["Duplicates"].iloc[0],Pos["Duplicates"].iloc[0]])
            
            
        
        End_Positions = np.array([End_Positions])
        End_Positions = pd.DataFrame(End_Positions[0],columns=["PlatePos","Gene_Position","Percentage", "Amount"])
        End_Positions["Percentage"] = pd.to_numeric(End_Positions["Percentage"])
        End_Positions = End_Positions.sort_values("Percentage")
        
        End_Pos_Best = np.array(End_Positions.iloc[-1:,:])
        
    
        Start_end= np.append(Start_Pos_Best,End_Pos_Best)
        Combined_NGS = np.vstack([Combined_NGS,Start_end])
        
    #Get the data out of the NGS:
        #plate position
        #Expected start position (based on most +-5 hits)
        #Start percentage (How many % of the hits are within +-5 bp)
        #Start amount (How many hits are in total)
        #Same with end
    NGS_Full= pd.DataFrame(Combined_NGS.T,["platePos","start_position","start_percentage", "start_amount","platePos","end_position","end_percentage", "end_amount"]).T
    
    NGS_Full["start_percentage"] =NGS_Full["start_percentage"].astype(float)
    NGS_Full["end_percentage"] =NGS_Full["end_percentage"].astype(float)
    NGS_Full["start_amount"] =NGS_Full["start_amount"].astype(int)
    NGS_Full["end_amount"] =NGS_Full["end_amount"].astype(int)
    NGS_Full["start_position"] =NGS_Full["start_position"].astype(int)
    NGS_Full["end_position"] =NGS_Full["end_position"].astype(int)
    
    #Filter 
    NGS_Filtered = NGS_Full[NGS_Full["start_percentage"]*NGS_Full["start_amount"]>2]
    NGS_Filtered = NGS_Filtered[NGS_Filtered["end_percentage"]*NGS_Filtered["end_amount"]>2]
    NGS_Filtered = NGS_Filtered[NGS_Filtered["start_percentage"]>0.15]
    NGS_Filtered = NGS_Filtered[NGS_Filtered["end_percentage"]>0.15]
    
    return NGS_Filtered

NGS_Filtered = NGS_Structure(Seq_Data)

C:\Users\askung\AppData\Local\Temp\ipykernel_11504\523715456.py:30: UserWarning: Boolean Series key will be reindexed to match DataFrame index.
  TestStart = Pos[Pos["alignment_genome_start"]>Start_Pos[0][copies]-5][Pos["alignment_genome_start"]<Start_Pos[0][copies]+5]
C:\Users\askung\AppData\Local\Temp\ipykernel_11504\523715456.py:30: UserWarning: Boolean Series key will be reindexed to match DataFrame index.
  TestStart = Pos[Pos["alignment_genome_start"]>Start_Pos[0][copies]-5][Pos["alignment_genome_start"]<Start_Pos[0][copies]+5]
C:\Users\askung\AppData\Local\Temp\ipykernel_11504\523715456.py:30: UserWarning: Boolean Series key will be reindexed to match DataFrame index.
  TestStart = Pos[Pos["alignment_genome_start"]>Start_Pos[0][copies]-5][Pos["alignment_genome_start"]<Start_Pos[0][copies]+5]
C:\Users\askung\AppData\Local\Temp\ipykernel_11504\523715456.py:46: UserWarning: Boolean Series key will be reindexed to match DataFrame index.
  TestEnd = Pos[Pos["alignment_genome_end"]>En

C:\Users\askung\AppData\Local\Temp\ipykernel_11504\523715456.py:46: UserWarning: Boolean Series key will be reindexed to match DataFrame index.
  TestEnd = Pos[Pos["alignment_genome_end"]>End_Pos[0][copies]-5][Pos["alignment_genome_end"]<End_Pos[0][copies]+5]
C:\Users\askung\AppData\Local\Temp\ipykernel_11504\523715456.py:46: UserWarning: Boolean Series key will be reindexed to match DataFrame index.
  TestEnd = Pos[Pos["alignment_genome_end"]>End_Pos[0][copies]-5][Pos["alignment_genome_end"]<End_Pos[0][copies]+5]
C:\Users\askung\AppData\Local\Temp\ipykernel_11504\523715456.py:46: UserWarning: Boolean Series key will be reindexed to match DataFrame index.
  TestEnd = Pos[Pos["alignment_genome_end"]>End_Pos[0][copies]-5][Pos["alignment_genome_end"]<End_Pos[0][copies]+5]
C:\Users\askung\AppData\Local\Temp\ipykernel_11504\523715456.py:46: UserWarning: Boolean Series key will be reindexed to match DataFrame index.
  TestEnd = Pos[Pos["alignment_genome_end"]>End_Pos[0][copies]-5][Pos["align

C:\Users\askung\AppData\Local\Temp\ipykernel_11504\523715456.py:30: UserWarning: Boolean Series key will be reindexed to match DataFrame index.
  TestStart = Pos[Pos["alignment_genome_start"]>Start_Pos[0][copies]-5][Pos["alignment_genome_start"]<Start_Pos[0][copies]+5]
C:\Users\askung\AppData\Local\Temp\ipykernel_11504\523715456.py:30: UserWarning: Boolean Series key will be reindexed to match DataFrame index.
  TestStart = Pos[Pos["alignment_genome_start"]>Start_Pos[0][copies]-5][Pos["alignment_genome_start"]<Start_Pos[0][copies]+5]
C:\Users\askung\AppData\Local\Temp\ipykernel_11504\523715456.py:30: UserWarning: Boolean Series key will be reindexed to match DataFrame index.
  TestStart = Pos[Pos["alignment_genome_start"]>Start_Pos[0][copies]-5][Pos["alignment_genome_start"]<Start_Pos[0][copies]+5]
C:\Users\askung\AppData\Local\Temp\ipykernel_11504\523715456.py:30: UserWarning: Boolean Series key will be reindexed to match DataFrame index.
  TestStart = Pos[Pos["alignment_genome_start"

C:\Users\askung\AppData\Local\Temp\ipykernel_11504\523715456.py:46: UserWarning: Boolean Series key will be reindexed to match DataFrame index.
  TestEnd = Pos[Pos["alignment_genome_end"]>End_Pos[0][copies]-5][Pos["alignment_genome_end"]<End_Pos[0][copies]+5]
C:\Users\askung\AppData\Local\Temp\ipykernel_11504\523715456.py:46: UserWarning: Boolean Series key will be reindexed to match DataFrame index.
  TestEnd = Pos[Pos["alignment_genome_end"]>End_Pos[0][copies]-5][Pos["alignment_genome_end"]<End_Pos[0][copies]+5]
C:\Users\askung\AppData\Local\Temp\ipykernel_11504\523715456.py:46: UserWarning: Boolean Series key will be reindexed to match DataFrame index.
  TestEnd = Pos[Pos["alignment_genome_end"]>End_Pos[0][copies]-5][Pos["alignment_genome_end"]<End_Pos[0][copies]+5]
C:\Users\askung\AppData\Local\Temp\ipykernel_11504\523715456.py:46: UserWarning: Boolean Series key will be reindexed to match DataFrame index.
  TestEnd = Pos[Pos["alignment_genome_end"]>End_Pos[0][copies]-5][Pos["align

C:\Users\askung\AppData\Local\Temp\ipykernel_11504\523715456.py:30: UserWarning: Boolean Series key will be reindexed to match DataFrame index.
  TestStart = Pos[Pos["alignment_genome_start"]>Start_Pos[0][copies]-5][Pos["alignment_genome_start"]<Start_Pos[0][copies]+5]
C:\Users\askung\AppData\Local\Temp\ipykernel_11504\523715456.py:30: UserWarning: Boolean Series key will be reindexed to match DataFrame index.
  TestStart = Pos[Pos["alignment_genome_start"]>Start_Pos[0][copies]-5][Pos["alignment_genome_start"]<Start_Pos[0][copies]+5]
C:\Users\askung\AppData\Local\Temp\ipykernel_11504\523715456.py:30: UserWarning: Boolean Series key will be reindexed to match DataFrame index.
  TestStart = Pos[Pos["alignment_genome_start"]>Start_Pos[0][copies]-5][Pos["alignment_genome_start"]<Start_Pos[0][copies]+5]
C:\Users\askung\AppData\Local\Temp\ipykernel_11504\523715456.py:30: UserWarning: Boolean Series key will be reindexed to match DataFrame index.
  TestStart = Pos[Pos["alignment_genome_start"

...

C:\Users\askung\AppData\Local\Temp\ipykernel_11504\523715456.py:46: UserWarning: Boolean Series key will be reindexed to match DataFrame index.
  TestEnd = Pos[Pos["alignment_genome_end"]>End_Pos[0][copies]-5][Pos["alignment_genome_end"]<End_Pos[0][copies]+5]
C:\Users\askung\AppData\Local\Temp\ipykernel_11504\523715456.py:46: UserWarning: Boolean Series key will be reindexed to match DataFrame index.
  TestEnd = Pos[Pos["alignment_genome_end"]>End_Pos[0][copies]-5][Pos["alignment_genome_end"]<End_Pos[0][copies]+5]
C:\Users\askung\AppData\Local\Temp\ipykernel_11504\523715456.py:46: UserWarning: Boolean Series key will be reindexed to match DataFrame index.
  TestEnd = Pos[Pos["alignment_genome_end"]>End_Pos[0][copies]-5][Pos["alignment_genome_end"]<End_Pos[0][copies]+5]
C:\Users\askung\AppData\Local\Temp\ipykernel_11504\523715456.py:48: UserWarning: Boolean Series key will be reindexed to match DataFrame index.
  TestEnd = TestEnd[TestEnd["alignment_genome_start"]>int(Start_Pos_Best[1])

C:\Users\askung\AppData\Local\Temp\ipykernel_11504\523715456.py:48: UserWarning: Boolean Series key will be reindexed to match DataFrame index.
  TestEnd = TestEnd[TestEnd["alignment_genome_start"]>int(Start_Pos_Best[1])-5][TestEnd["alignment_genome_start"]<int(Start_Pos_Best[1])+5]
C:\Users\askung\AppData\Local\Temp\ipykernel_11504\523715456.py:46: UserWarning: Boolean Series key will be reindexed to match DataFrame index.
  TestEnd = Pos[Pos["alignment_genome_end"]>End_Pos[0][copies]-5][Pos["alignment_genome_end"]<End_Pos[0][copies]+5]
C:\Users\askung\AppData\Local\Temp\ipykernel_11504\523715456.py:48: UserWarning: Boolean Series key will be reindexed to match DataFrame index.
  TestEnd = TestEnd[TestEnd["alignment_genome_start"]>int(Start_Pos_Best[1])-5][TestEnd["alignment_genome_start"]<int(Start_Pos_Best[1])+5]
C:\Users\askung\AppData\Local\Temp\ipykernel_11504\523715456.py:48: UserWarning: Boolean Series key will be reindexed to match DataFrame index.
  TestEnd = TestEnd[TestEnd[

C:\Users\askung\AppData\Local\Temp\ipykernel_11504\523715456.py:46: UserWarning: Boolean Series key will be reindexed to match DataFrame index.
  TestEnd = Pos[Pos["alignment_genome_end"]>End_Pos[0][copies]-5][Pos["alignment_genome_end"]<End_Pos[0][copies]+5]
C:\Users\askung\AppData\Local\Temp\ipykernel_11504\523715456.py:48: UserWarning: Boolean Series key will be reindexed to match DataFrame index.
  TestEnd = TestEnd[TestEnd["alignment_genome_start"]>int(Start_Pos_Best[1])-5][TestEnd["alignment_genome_start"]<int(Start_Pos_Best[1])+5]
C:\Users\askung\AppData\Local\Temp\ipykernel_11504\523715456.py:46: UserWarning: Boolean Series key will be reindexed to match DataFrame index.
  TestEnd = Pos[Pos["alignment_genome_end"]>End_Pos[0][copies]-5][Pos["alignment_genome_end"]<End_Pos[0][copies]+5]
C:\Users\askung\AppData\Local\Temp\ipykernel_11504\523715456.py:48: UserWarning: Boolean Series key will be reindexed to match DataFrame index.
  TestEnd = TestEnd[TestEnd["alignment_genome_start"

C:\Users\askung\AppData\Local\Temp\ipykernel_11504\523715456.py:46: UserWarning: Boolean Series key will be reindexed to match DataFrame index.
  TestEnd = Pos[Pos["alignment_genome_end"]>End_Pos[0][copies]-5][Pos["alignment_genome_end"]<End_Pos[0][copies]+5]
C:\Users\askung\AppData\Local\Temp\ipykernel_11504\523715456.py:46: UserWarning: Boolean Series key will be reindexed to match DataFrame index.
  TestEnd = Pos[Pos["alignment_genome_end"]>End_Pos[0][copies]-5][Pos["alignment_genome_end"]<End_Pos[0][copies]+5]
C:\Users\askung\AppData\Local\Temp\ipykernel_11504\523715456.py:48: UserWarning: Boolean Series key will be reindexed to match DataFrame index.
  TestEnd = TestEnd[TestEnd["alignment_genome_start"]>int(Start_Pos_Best[1])-5][TestEnd["alignment_genome_start"]<int(Start_Pos_Best[1])+5]
C:\Users\askung\AppData\Local\Temp\ipykernel_11504\523715456.py:46: UserWarning: Boolean Series key will be reindexed to match DataFrame index.
  TestEnd = Pos[Pos["alignment_genome_end"]>End_Pos[

C:\Users\askung\AppData\Local\Temp\ipykernel_11504\523715456.py:30: UserWarning: Boolean Series key will be reindexed to match DataFrame index.
  TestStart = Pos[Pos["alignment_genome_start"]>Start_Pos[0][copies]-5][Pos["alignment_genome_start"]<Start_Pos[0][copies]+5]
C:\Users\askung\AppData\Local\Temp\ipykernel_11504\523715456.py:30: UserWarning: Boolean Series key will be reindexed to match DataFrame index.
  TestStart = Pos[Pos["alignment_genome_start"]>Start_Pos[0][copies]-5][Pos["alignment_genome_start"]<Start_Pos[0][copies]+5]
C:\Users\askung\AppData\Local\Temp\ipykernel_11504\523715456.py:30: UserWarning: Boolean Series key will be reindexed to match DataFrame index.
  TestStart = Pos[Pos["alignment_genome_start"]>Start_Pos[0][copies]-5][Pos["alignment_genome_start"]<Start_Pos[0][copies]+5]
C:\Users\askung\AppData\Local\Temp\ipykernel_11504\523715456.py:30: UserWarning: Boolean Series key will be reindexed to match DataFrame index.
  TestStart = Pos[Pos["alignment_genome_start"

In [ ]:
def demultiplex_to_lum(Output_Path, luminescence_path, First_primer_used,ORF_Length):
    #Read data from demultiplexer
    After = pd.read_csv(f'{Output_Path}/after_demultiplex.csv',sep=",")
    
    #Fix up data
    Seq_Data=After.sort_values("Positions")
    #Remove non-aligned
    Seq_Data= Seq_Data[Seq_Data["alignment_genome"]!="*"]

    #Find all plate positions
    Positions = [Seq_Data.Positions.unique()]
    
    #Array to fill data about probable position into, added a 0-array to start
    Combined_NGS = np.array([0,0,0,0,0,0,0,0])

    #Loop that goes through all the found plate-positions 
    for platepositions in range(len(Positions[0])):
        Start_Positions = []
        End_Positions = []
        
        Pos = Seq_Data[Seq_Data["Positions"]==Positions[0][platepositions]]
    
        Start_Pos = [Pos.alignment_genome_start.unique()]
        End_Pos = [Pos.alignment_genome_end.unique()]
        #The following code goes through start positions
        #Teststart gets fixed so it tests how many are at +- 5 bases on each side (Expecting minor errors)
        for copies in range(len(Start_Pos[0])):
            len_total = len(Pos)

            TestStart = Pos[Pos["alignment_genome_start"]>(Start_Pos[0][copies]-5)][Pos["alignment_genome_start"]<(Start_Pos[0][copies]+5)]
            Start_Pos_Predicter = (TestStart["alignment_genome_start"].value_counts())
            Len_Start = len(TestStart["alignment_genome_start"])

            Start_Positions.append([Positions[0][platepositions],Start_Pos_Predicter.index[0],Len_Start/len_total,Pos["Duplicates"].iloc[0]])
        
        
        Start_Positions = np.array([Start_Positions])
        Start_Positions = pd.DataFrame(Start_Positions[0],columns=["PlatePos","Gene_Position","Percentage", "Amount"])
        
        Start_Positions["Percentage"] = pd.to_numeric(Start_Positions["Percentage"])
        #It sorts to put the best choice in the end
        Start_Positions = Start_Positions.sort_values("Percentage")
        ##Here it chooses the best start-position
        Start_Pos_Best = np.array(Start_Positions.iloc[-1,:])

        #Does the same for the end-positions
        for copies in range(len(End_Pos[0])):
            len_total = len(Pos)
            TestEnd = Pos[Pos["alignment_genome_end"]>End_Pos[0][copies]-5][Pos["alignment_genome_end"]<End_Pos[0][copies]+5]
            ###A test to remove the ones that don´t fit with the Fw. primer
            TestEnd = TestEnd[TestEnd["alignment_genome_start"]>int(Start_Pos_Best[1])-5][TestEnd["alignment_genome_start"]<int(Start_Pos_Best[1])+5]
            End_Pos_Predicter = (TestEnd["alignment_genome_end"].value_counts())
            Len_end = len(TestEnd["alignment_genome_end"])
    
            if Len_end>0:
                End_Positions.append([Positions[0][platepositions],End_Pos_Predicter.index[0],Len_end/len_total,Pos["Duplicates"].iloc[0]])
            
            
        
        End_Positions = np.array([End_Positions])
        End_Positions = pd.DataFrame(End_Positions[0],columns=["PlatePos","Gene_Position","Percentage", "Amount"])
        End_Positions["Percentage"] = pd.to_numeric(End_Positions["Percentage"])
        End_Positions = End_Positions.sort_values("Percentage")
        
        End_Pos_Best = np.array(End_Positions.iloc[-1:,:])

        Start_end= np.append(Start_Pos_Best,End_Pos_Best)
        Combined_NGS = np.vstack([Combined_NGS,Start_end])
        
    #This is the full dataframe with start and end-data implemented
    NGS_Full= pd.DataFrame(Combined_NGS.T,["platePos","start_position","start_percentage", "start_amount","platePos","end_position","end_percentage", "end_amount"]).T
    
    #Set data types
    NGS_Full["start_percentage"] =NGS_Full["start_percentage"].astype(float)
    NGS_Full["end_percentage"] =NGS_Full["end_percentage"].astype(float)
    NGS_Full["start_amount"] =NGS_Full["start_amount"].astype(int)
    NGS_Full["end_amount"] =NGS_Full["end_amount"].astype(int)
    NGS_Full["start_position"] =NGS_Full["start_position"].astype(int)
    NGS_Full["end_position"] =NGS_Full["end_position"].astype(int)

    #Filter: Removes the samples which are not found with above parameters. 
    #Might be unnescessary due to the QC in demultiplexer
    NGS_Filtered = NGS_Full[(NGS_Full["start_percentage"]*NGS_Full["start_amount"])>5]
    NGS_Filtered = NGS_Filtered[(NGS_Filtered["end_percentage"]*NGS_Filtered["end_amount"])>5]
    NGS_Filtered = NGS_Filtered[NGS_Filtered["start_percentage"]>0.30]
    NGS_Filtered = NGS_Filtered[NGS_Filtered["end_percentage"]>0.30]
    #Just to make sure that a few point-mutations in the end dont get lost, it is put at orf+5
    #The following removes accidental inserts from the backbone which has been seen rarely. 
    NGS_Filtered = NGS_Filtered[NGS_Filtered["end_position"]<(ORF_Length+5)] 

    
    
    #Luminescence_Implementation############################################################
    #Data from full cell below: 
    
    #Input for this:
    NGS = NGS_Filtered
    Lum =luminescence_path
    Primer = First_primer_used   
    
    FullCell = glob.glob(os.path.join(Lum,"Luciferase_FC_Plate*.xls"))

    Full_Filler = []
    for f in FullCell:
        List_Filter=[] 
        # read the csv file 
        Filter_Data =(pd.read_excel(f).iloc[-96:,2:]).reset_index() #Yields gen5 data

        #A bit of goofy code, should be redone but doesn´t hurt the script speed:
        for i in range(96): 
            List_Filter.append(Filter_Data.iloc[i,1])
        #Redefine positions of data so it fits with "normal" A1, B1...G12, H12 format

        List_Filter2 = []
        for i in range(12):
            for j in range(8):
                List_Filter2.append(List_Filter[(j*12)+(i)])
        #Define plate and loop

        PlateNumber=re.search('_Plate(.*)Time_', f)
        Full_Filler.append([PlateNumber.group(1),List_Filter2])
    #Make data for "Full_Cell"
    Full_Info= []
    Full_columns= []
    
    for i in range(len(Full_Filler)):
        Full_Info.append(Full_Filler[i][1])
        Full_columns.append(Full_Filler[i][0])
    
    Full_Info = np.array(Full_Info).T    
    Full_Info = pd.DataFrame(Full_Info,columns=Full_columns)
    ###End_Full_Cell###

    #Data from cytosol below: 
    Cytosol = glob.glob(os.path.join(Lum,"Luciferase_Cytosol_*.xls"))
    Cytosol_Filler = []
    for f in Cytosol:
        List_Filter=[] 
        # read the csv file 
        Filter_Data =(pd.read_excel(f).iloc[-96:,2:]).reset_index()

        for i in range(96):
            List_Filter.append(Filter_Data.iloc[i,1])
        
        #Redefine positions of data so it fits with "normal" A1, B1...G12, H12 format
        
        List_Filter2 = []
        for i in range(12):
            for j in range(8):
                List_Filter2.append(List_Filter[(j*12)+(i)])
        #Define plate and loop

        
        #Define plate and loop
        PlateNumber=re.search('_Plate(.*)Time_', f)
        Cytosol_Filler.append([PlateNumber.group(1),List_Filter2])
    
    Cytosol_Info= []
    cytosol_columns = []
    #Cytosol_Filler=np.array(Cytosol_Filler)
    for i in range(len(Cytosol_Filler)):
        Cytosol_Info.append(Cytosol_Filler[i][1])
        cytosol_columns.append(Cytosol_Filler[i][0])
    
    Cytosol_Info = np.array(Cytosol_Info).T
    Cytosol_Info = pd.DataFrame(Cytosol_Info,columns=cytosol_columns)
    ###End_Cytosol###
    #Combine above to a readable dataframe
    
    Insertion_array = np.array([0,0,0])
    for i in range(len(Cytosol)):
        Cytosol_plate = Cytosol_Info[f'{i+1}']
        Full_plate = Full_Info[f'{i+1}']
        for j in range(96):
            Position =  f"{i+Primer}"+","+f"{j+1}"
            Cytosol_Lum = Cytosol_plate[j]
            Full_Lum = Full_plate[j]
            Insertion_point = np.array([Position,Cytosol_Lum,Full_Lum])
            Insertion_array = np.vstack([Insertion_array,Insertion_point])

    Insertion_array = pd.DataFrame(Insertion_array,columns=["platePos","Cytosol","Full_Cell"])
    Insertion_DF=Insertion_array[Insertion_array["platePos"]!=0]

    NGS_Filtered = NGS.iloc[:,1:]
    NGS_Filtered["platePos"] = NGS_Filtered["platePos"].astype(str)
    Insertion_DF["platePos"] = Insertion_DF["platePos"].astype(str)

    NGS_Filtered = NGS_Filtered.merge(Insertion_DF, left_on='platePos', right_on ='platePos' )

    ###############This part extracts OD-data and implements it in the data#############
    pattern = "OD_Plate*.xlsx"
    # Use glob to get all the files matching the pattern
    files = glob.glob(f"{luminescence_path}\\{pattern}")


    ####Data from growth cultures###########
    # Create a dictionary to store all the dataframes with their coresponding file names as keys
    dfs = {}

    # Read each excel file into a pandas DataFrame and store it in the dictionary
    for file in files:
        # Extract the file number from the file name to use as a key
        file_num = file.split('OD_Plate')[1].split('.xlsx')[0]
        
        # Read the Excel file into a DataFrame
        dfs[file_num] = pd.read_excel(file)


    letters = ["A", "B", "C", "D", "E", "F", "G", "H"]

    OD_data = np.array(["","","","",""])

    for plates in range(len(dfs)):
        posnumber = 1
        for j in range(12):
            for i in range(8):
                #Get the time and 
                A= dfs[f"{plates+1}"]["Time"][:5]
                B= dfs[f"{plates+1}"][f"{letters[i]}{j+1}"][:5]
                plt.plot(A,B)
                trap1=np.trapz(B,A)
                #print(trap)
                
                A= dfs[f"{plates+1}"]["Time"][4:]
                B= dfs[f"{plates+1}"][f"{letters[i]}{j+1}"][4:]
                plt.plot(A,B)
                trap2=np.trapz(B-dfs[f"{plates+1}"][f"{letters[i]}{j+1}"][4],A)
                
                OD_data = np.vstack((OD_data, np.array([f"{letters[i]}{j+1}",plates+Primer,f"{plates+Primer,posnumber}",trap1,trap2])))
                
                posnumber+=1
            
    #############Here is pre-OD-Data

    #Data from pre-culture:
    Pre_exp = glob.glob(f"{luminescence_path}\\Pre_Experiment_Data_Loop__Plate_*.xls")
    pre_temp = []
    predata_total = np.array(["","",""])
    for f in Pre_exp:
        List_Filter=[] 
        List_pos = []
        # read the csv file
        predata_plate =pd.read_excel(f).iloc[-96:,3]
        if len(predata_plate)==96:
            for i in range(96):
                List_Filter.append(predata_plate.iloc[i])
        
        predata_pos =pd.read_excel(f).iloc[-96:,2]
        if len(predata_pos)==96:
            for i in range(96):
                List_pos.append(predata_pos.iloc[i])

            #Define plate and loop
            Loopnumber=re.search('_Loop_(.*)_', f)
            ###Adding "Primer-1" to fix if the second primerset is used
            PlateNumber= re.search('_Plate_(.*)Time_Date_', f)

            Time_Date = re.search('Time_Date_(.*).xls', f)
            #Extract data from above and combine it (Primer is added to fit with "Real" position)
            pre_temp=([int(PlateNumber.group(1))+Primer-1,List_pos,List_Filter])

            predata=pd.DataFrame(np.array([np.repeat(pre_temp[0],96),pre_temp[1],pre_temp[2]])).T
        predata_total = np.vstack((predata_total,predata))

    od_df = pd.DataFrame(OD_data,columns=["pos","plate","platePos","preinduction_auc","postinduction_auc"])
    pre_df = pd.DataFrame(predata_total,columns=["plate","pos","pre_od"])
    merged_od = pd.merge(od_df, pre_df, on=['plate', 'pos'])
    ###Prep the platePos  for merge
    merged_od['platePos'] = merged_od['platePos'].str.replace('(', '').str.replace(')', '').str.replace(' ','')

    NGS_Filtered = pd.merge(merged_od, NGS_Filtered, on=['platePos'])    
    NGS_Filtered.to_csv(f'{Output_Path}/NGS_Filtered.csv', index = False)

    return NGS_Filtered
NGS_Filtered = demultiplex_to_lum(Alignment_Data, luminescence_path, First_primer_used, ORF_Length)
##Problem: Loads twice on calm?### test random stuff in "return"

In [11]:
##########OLD CODE#########################
# -*- coding: utf-8 -*-
"""
Created on Fri Dec 22 10:08:21 2023

@author: askung
"""

#Luminescence_Implementation############################################################
#Data from full cell below: 


def Luminescence_Structure(Lum,Primer,NGS):    

    FullCell = glob.glob(os.path.join(Lum,"Luciferase_FC_Plate*.xls"))
    Full_Filler = []
    for f in FullCell:
        List_Filter=[] 
        # read the csv file 
        Filter_Data =(pd.read_excel(f).iloc[-96:,2:]).reset_index()
    
        for i in range(96):
            List_Filter.append(Filter_Data.iloc[i,1])
    
        #Define plate and loop
    
        PlateNumber=re.search('_Plate(.*)Time_', f)
        Full_Filler.append([PlateNumber.group(1)[0],List_Filter])
    #Make data for "Full_Cell"
    Full_Info= []
    
    Full_Filler=np.array(Full_Filler)
    for i in range(8):
        Full_Info.append(Full_Filler[i][1])
    
    Full_Info = np.array(Full_Info).T    
    Full_Info = pd.DataFrame(Full_Info,columns=["1","2","3","4","5","6","7","8"])
    ###End_Full_Cell###
    
    #Data from cytosol below: 
    
    Cytosol = glob.glob(os.path.join(Lum,"Luciferase_Cytosol_*.xls"))
    Cytosol_Filler = []
    for f in Cytosol:
        List_Filter=[] 
        # read the csv file 
        Filter_Data =(pd.read_excel(f).iloc[-96:,2:]).reset_index()
    
        for i in range(96):
            List_Filter.append(Filter_Data.iloc[i,1])
    
        #Define plate and loop
    
        PlateNumber=re.search('_Plate(.*)Time_', f)
        Cytosol_Filler.append([PlateNumber.group(1)[0],List_Filter])
    
    Cytosol_Info= []
    
    Cytosol_Filler=np.array(Cytosol_Filler)
    for i in range(8):
        Cytosol_Info.append(Cytosol_Filler[i][1])
    
    Cytosol_Info = np.array(Cytosol_Info).T
    Cytosol_Info = pd.DataFrame(Cytosol_Info,columns=["1","2","3","4","5","6","7","8"])
    ###End_Cytosol###
    
    #Combine above to a readable dataframe
    
    Insertion_array = np.array([0,0,0])
    for i in range(len(Cytosol)):
        Cytosol_plate = Cytosol_Info[f'{i+1}']
        Full_plate = Full_Info[f'{i+1}']
        for j in range(96):
            Position =  f"{i+Primer}"+","+f"{j+1}"
            Cytosol_Lum = Cytosol_plate[j]
            Full_Lum = Full_plate[j]
            Insertion_point = np.array([Position,Cytosol_Lum,Full_Lum])
            Insertion_array = np.vstack([Insertion_array,Insertion_point])
    
    Insertion_array = pd.DataFrame(Insertion_array,columns=["platePos","Cytosol","Full_Cell"])
    Insertion_DF=Insertion_array[Insertion_array["platePos"]!=0]
    
    
    
    NGS_Filtered = NGS.iloc[:,1:]
    NGS_Filtered["platePos"] = NGS_Filtered["platePos"].astype(str)
    Insertion_DF["platePos"] = Insertion_DF["platePos"].astype(str)
    
    NGS_Filtered = NGS_Filtered.merge(Insertion_DF, left_on='platePos', right_on ='platePos' )
    ######################################
    return NGS_Filtered


#Plotter: 
def seq_lum_plots(ORF_Length,NGS): 
    #Go through the data and extract all the start/end/size data: 
    Data_Distribution = []
    for i in range((NGS["start_percentage"].size)):
        Data_Distribution.append([NGS_Filtered["start_position"].iloc[i],NGS_Filtered["end_position"].iloc[i],NGS_Filtered["end_position"].iloc[i]-NGS_Filtered["start_position"].iloc[i]])
    #Create the data for plotting:
    Plotting_info=[]
    #Make Data_Distribution into dataframe
    Data_Distribution= np.asarray(Data_Distribution)
    
    Data_Distribution=pd.DataFrame(Data_Distribution,columns=["Start","Stop","Length"])
    
    #Go through the size of Data_Distribution, At every point gain size-data for each base
    for i in range(len(Data_Distribution["Start"])):
        for j in range(Data_Distribution["Start"][i],Data_Distribution["Stop"][i]):
            Full_cell=((np.array([NGS_Filtered["Full_Cell"][i]]).astype(float)))
            Cytosol=((np.array([NGS_Filtered["Cytosol"][i]]).astype(float)))
            Plotting_info.append([j,Data_Distribution["Length"][i],Full_cell,Cytosol])
        #if i>200: #Break to not break my computer :D 
        #    break
    #Make plotting info into dataframe
    Plotting_info2=np.asarray(Plotting_info)
    Plotting_info2=pd.DataFrame(Plotting_info2,columns=["Base","Length","Full_Cell","Cytosol"])
    
    #Extra high outlier removal below: 
    #Plotting_info2=Plotting_info2[Plotting_info2["Full_Cell"]<1000]
    #Plotting_info2=Plotting_info2[Plotting_info2["Cytosol"]<1000]
    
    
    #Colour the plot by luminescence
    
    #Plot the thing! 
    #sns.scatterplot(Data=Plotting_info2,x=P"Base",y="Length")
    plt.scatter(Plotting_info2["Base"],Plotting_info2["Length"],c=Plotting_info2["Full_Cell"], cmap='coolwarm',s=0.1)
    plt.title("Full cell")
    plt.xlabel("Base_Number")
    plt.ylabel("Size")
    plt.xlim([0,ORF_Length])
    plt.ylim([0,ORF_Length])
    plt.colorbar()
    ###Issue with colour!##
    
    plt.show()
    
    plt.scatter(Plotting_info2["Base"],Plotting_info2["Length"],c=Plotting_info2["Cytosol"], cmap='coolwarm',s=0.1)
    plt.title("Cytosol")
    plt.xlabel("Base_Number")
    plt.ylabel("Size")
    plt.xlim([0,ORF_Length])
    plt.ylim([0,ORF_Length])
    plt.colorbar()
    ###Issue with colour!##
    
    plt.show()


NGS_Filtered = Luminescence_Structure(luminescence_path,First_primer_used,NGS_Filtered)
seq_lum_plots(ORF_Length,NGS_Filtered)    

NGS_Filtered.to_csv(f'{Output_Path}/NGS_Filtered.csv', index = False)

    platePos  start_position  start_percentage  start_amount platePos  \
2      17,12             916          0.272727            11    17,12   
3      17,13             433          0.868421           114    17,13   
4      17,14             433          0.900000            30    17,14   
6      17,18             448          0.591160           362    17,18   
7      17,19             262          0.733645           428    17,19   
..       ...             ...               ...           ...      ...   
384    24,66             250          0.816310          1263    24,66   
385    24,68              22          0.453763           465    24,68   
387    24,70             881          0.554545           660    24,70   
392    24,77            1072          0.381503           346    24,77   
393    24,78             178          0.527697           686    24,78   

     end_position  end_percentage  end_amount  
2            1446        0.272727          11  
3             654        0.